In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import datetime

In [2]:
cad = pd.read_csv('data\\BD_Linhas-de-Transmissão(Cadastro).csv', encoding='latin', sep=';')
med = pd.read_csv('data\\BD_Linhas-de-Transmissão(Documentos de Medição).csv', encoding='latin', sep=';', dtype=object)


med[['Valor teórico',
     'LimInfIntMed.',
     'LimSupIntMed.',
     'ValMed/PosTCont']] = med[['Valor teórico',
     'LimInfIntMed.',
     'LimSupIntMed.',
     'ValMed/PosTCont']].replace({r'\.':'',',':'.'}, regex=True)
     
med[['Valor teórico',
     'LimInfIntMed.',
     'LimSupIntMed.',
     'ValMed/PosTCont']] = med[['Valor teórico',
     'LimInfIntMed.',
     'LimSupIntMed.',
     'ValMed/PosTCont']].astype(float)
     
med[['Equipamento',
     'Ponto medição',
     'Doc.medição']] = med[['Equipamento',
     'Ponto medição',
     'Doc.medição']].astype(int)
     
med['Data'] = pd.to_datetime(med['Data'], dayfirst=True)


cad[['Latitude', 'Longitude']] = cad[['Latitude', 'Longitude']].replace({r'\.':'',',':'.', '#N/D': 'NaN'}, regex=True)

cad[['Latitude', 'Longitude']] = cad[['Latitude', 'Longitude']].astype(float)

cad[['Equipamento', 'Tensão']] = cad[['Equipamento', 'Tensão']].astype(int)

In [3]:
dt = med[['Equipamento', 'Ponto medição', 'Item medição','Denominação', 'Txt.code codif.']]
dt = dt.rename(columns={'Equipamento':'equip', 'Ponto medição':'ponto', 'Item medição':'item','Denominação':'denom','Txt.code codif.':'text'})

In [4]:
dt.denom.unique()

array(['ROCADA MECANIZADA', 'ROCADA MANUAL', 'PODA',
       'CABO CONDUTOR (DIR/UNI)', 'Qualificacao do Equipamento',
       'ENTULHO', 'TENTO ROMP-INF/DIR/EXTER(CIRC DIR/UNI)',
       'TENTO ROMP-INF/DIR/EXTER(CIRC ESQ)',
       'TENTO ROMP-MEIO/INTER(CIRC DIR/UNI)',
       'TENTO ROMP-MEIO/INTER(CIRC ESQ)', 'TENTO ROMPIDO(DIR/UNI)',
       'TENTO ROMPIDO(ESQ)', 'CABO PARA-RAIO (DIR/UNI)',
       'CABO PARA-RAIO (ESQ)', 'PROTECAO ANTICORROSIVA',
       'CORROSAO CABO PARA-RAIO (DIR/UNI)', 'PLACA',
       'CORROSAO NA ESTRUTURA', 'BOBINA DE BLOQUEIO (DIR/UNI)',
       'CARGA RUPTURA-INF/DIR/EXTER(CIRC ESQ)',
       'FERRAGENS/CONECTORES CONDUTOR (ESQ)', 'DISTANCIA ATE BURACO',
       'BASE SUJA', 'EMENDA/REPARO CONDUTOR (DIR/UNI)',
       'JUMPER (DIR/UNI)', 'CORRO. GRAMPO SUSP. CONDUTOR (DIR/UNI)',
       'CORRO. GRAMPO SUSP. CONDUTOR (ESQ)', 'ESTRUTURA', 'INVASAO',
       'NINHO DE PÁSSARO', 'ESFERA (DIR/UNI)', 'RABICHO (ESQ)',
       'DISTANCIA DO CABO A VEGETACAO',
       'ISOL - I

In [5]:
import re
from unidecode import unidecode

def filter_text(text):
    # print(text)
    text = text.upper()
    text = unidecode(text)
    
    # Filtro tokens inúteis
    # (?<=\s)NO( |$)|
    # (?<=\s)DO( |$)|
    # (?<=\s)E( |$)|
    # \.|(D:)
    # ()|"|.|:
    # espaços seguidos ou inúteis
    text = re.sub(r'(?<=\s)N(A|O)( |$)|(?<=\s)EM( |$)|(?<=\s)D(A|E|O)( |$)|(?<=\s)E( |$)|(D:)|\/( |$)',' ', text)
    text = re.sub(r'\(|\)|\.|:|"',' ', text)
    text = re.sub(r'(^\s+)|(\s{1,})(?=\s\S)|(\s+$)', '', text)
    
    # Fitro T**
    # ((?<=T)(\D|)(?=\d+))
    text = re.sub(fr'((?<=T)(\D|)(?=\d{1,}))', '', text)
    
    # Completar palavras cortadas padrão
    # Fases
    if match := re.search(r'((?<= )FASE\s)([A-Z]{1,}(?=\s|$))', text):
        fase = match.group(2)
        text = text[:match.span()[0]] + text[match.span()[1]:]
        # Match com as possiblidades
        if fase[0] == 'S':
            fase = 'SUPERIOR'
        elif fase[0] == 'M' or fase[0] == 'C':
            fase = 'MEIO'
        elif fase[0] == 'V':
            fase = 'VERMELHA'
        elif fase[0] == 'B':
            fase = 'BRANCA'
        elif len(fase) > 1:
            if fase[:2] == 'EX':
                fase = 'EXTERNA'
            elif fase[:2] == 'ES':
                fase = 'ESQUERDA'
            elif fase[:2] == 'DI':
                fase = 'DIREITA'
            elif len(fase) > 2:
                if fase[:2] == 'IN':
                    if fase[2] == 'F':
                        fase = 'INFERIOR'
                    elif len(fase) > 5:
                        if fase[5] == 'N':
                            fase = 'INTERNA'
                        elif fase[5] == 'M':
                            fase = 'INTERMEDIARIA'
        # inconclusiva => excluir
        else: fase = ''
        text = text + ' ' + fase
        
    # Lado
    if match := re.search(r'((?<= )LADO\s)([A-Z]{1,}(?=\s|$))', text):
        lado = match.group(2)
        text = text[:match.span()[0]] + text[match.span()[1]:]
        # Match com as possiblidades
        if lado[0] == 'V':
            lado = 'VIVO'
        elif lado[0] == 'M':
            lado = 'MORTO'
        elif len(lado) > 1:
            if lado[:2] == 'ES':
                lado = 'ESQUERDO'
            elif lado[:2] == 'DI':
                lado = 'DIREITO'
            elif lado[:2] == 'IN':
                lado = 'INFERIOR'
            elif lado[:2] == 'EN':
                lado = 'ENERGIZADO'
            elif lado[:2] == 'DE':
                lado = 'DESENERGIZADO'
        elif lado == 'CAV' or lado == 'CPV':
            lado = lado
        # inconclusiva => excluir
        else: lado = ''
        text = text + ' ' + lado
    
    # termos comuns:
    text = re.sub(r'DI GUEDES', 'DIGUEDES', text)
    
    # print(denom)
    # print(item)
    # print(text)
    return text

def empty_spaces(text):
    tags = re.split(r'\. |\/| | - ', text)
    
    for i in range(len(tags)):
        if tags[i] == None: continue
        # Remoção de ' ' duplicados e inúteis
        # só ta dando match no primeiro :(
        tags[i] = re.sub(r'(^\s+)|(\s{1,})(?=\s\S)|(\s+$)', '', tags[i])
    tags = list(filter(None, tags))
    print(tags)
    return tags

In [6]:
texts = dt['text'].fillna('').apply(lambda x: filter_text(x))

In [7]:
dt['text'].str.contains('ISOLADORE').value_counts()

text
False    244269
Name: count, dtype: int64

In [8]:
dt.dropna().loc[dt.dropna()['text'].str.contains('final'), 'text'].unique()

array([], dtype=object)

In [9]:
import spacy

if 'pt_core_news_sm' not in spacy.util.get_installed_models():
    spacy.cli.download('pt_core_news_sm')

# Tokenização
nlp = spacy.load('pt_core_news_sm')

In [10]:
tags = texts.apply(lambda x: empty_spaces(x))

['FIM', 'VAO']
['INICIO', 'VAO']
['MEIO', 'FIM', 'VAO']
['MEIO', 'FIM', 'VAO']
['VAO', 'COMPLETO']
['VAO', 'COMPLETO']
['INICIO', 'MEIO', 'VAO']
['FIM', 'VAO']
['VAO', 'COMPLETO']
['INICIO', 'MEIO', 'VAO']
['INICIO', 'MEIO', 'VAO']
['MEIO', 'VAO']
['INICIO', 'VAO']
['VAO', 'COMPLETO']
['VAO', 'COMPLETO']
['INICIO', 'MEIO', 'VAO']
['MEIO', 'FIM', 'VAO']
['MEIO', 'VAO']
['MEIO', 'VAO']
['FIM', 'VAO']
['MEIO', 'VAO']
['MEIO', 'VAO']
['CONDICAO', 'NORMAL']
[]
[]
['CONDICAO', 'NORMAL']
[]
[]
[]
['RISCO', 'FUTURO']
['CONDICAO', 'NORMAL']
[]
[]
['CONDICAO', 'NORMAL']
['CONDICAO', 'NORMAL']
['CONDICAO', 'NORMAL']
['CONDICAO', 'NORMAL']
['CONDICAO', 'NORMAL']
['CONDICAO', 'NORMAL']
['CONDICAO', 'NORMAL']
['CONDICAO', 'NORMAL']
['CONDICAO', 'NORMAL']
[]
[]
[]
['CONDICAO', 'NORMAL']
['FIM', 'VAO']
['CONDICAO', 'NORMAL']
['CONDICAO', 'NORMAL']
['CONDICAO', 'NORMAL']
['CONDICAO', 'NORMAL']
['CONDICAO', 'NORMAL']
['CONDICAO', 'NORMAL']
['CONDICAO', 'NORMAL']
['CONDICAO', 'NORMAL']
['FALTANDO']
[]
[]

In [11]:
temp = [x for y in tags for x in y]
unique_tags = list(set(temp))
count = dict((x, temp.count(x)) for x in unique_tags)
frequency = {k:v for k,v in sorted(count.items(), key=lambda item: item[1], reverse=False)}

from Levenshtein import distance, ratio
keys = list(frequency.keys())
# keys = ['avant','avante']
for i in range(len(keys)):
    h0 = keys[i]
    if not h0.isalpha(): continue
    for j in range(i+1,len(keys)):
        h1 = keys[j]
        # primeiro caracter é igual
        if h0[0] == h1[0]:
            if h0 in h1:
                if (distance(h0, h1) <= len(h0)/2):
                    h0 = h1
            elif (distance(h0, h1) == 1):
                left = 0
                right = 0
                if h0[-1] in ['S', 'A', 'O']:
                    left += 1
                    if h0[-2:] in ['AS','OS']:
                        left += 1
                if h1[-1] in ['S', 'A', 'O']: 
                    right += 1
                    if h1[-2:] in ['AS','OS']:
                        right += 1
                if left > 0 and right > 0:
                    if (distance(h0[:-(left)], h1[:-(right)]) == 0): 
                        # print(h0, left, h1, right, distance(h0[:-(left)], h1[:-(right)]))
                        h0=h1
            elif (ratio(h0, h1) > 0.8):
                h0 = h1
    
    temp = [h0 if x == keys[i] else x for x in temp]

In [12]:
unique_tags = list(set(temp))
matrix = np.zeros((len(tags), len(unique_tags)))
j = 0
for i in range(len(tags)):
    words = temp[j:j+len(tags[i])]
    matrix[i] = [1 if x in words else 0 for x in unique_tags]
    j += len(tags[i])
wordbox = pd.DataFrame(matrix, columns=unique_tags)

In [16]:
wordbox.sum()

RISCO         22885.0
I             43999.0
ESFORCO          53.0
FROUXO          668.0
ENGAIOLADO       27.0
               ...   
FALTANDO       3925.0
-              8454.0
BOBINA            6.0
UNILATERAL       53.0
DETRITOS          3.0
Length: 119, dtype: float64